<a href="https://colab.research.google.com/github/MengqiLI0907/Wildfire/blob/main/Wildfire.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Using Python for **military** geoanalytics tasks in Russia.

I utilize information from the **Fire Information for Resource Management System (FIRMS)** developed at the University of Maryland with support from NASA and the UN in 2007. FIRMS allows real-time monitoring of active fires worldwide, utilizing data from Aqua and Terra satellites equipped with MODIS spectroradiometers and VIIRS on S-NPP and NOAA 20 satellites.

I have employedng FIRMS data to identify fires within the territory of russian military facilitie**s since 20-02-20 before the Russo–Ukrainian War**22.

In [ ]:
from google.colab import drive
drive.mount('/content/drive')
military_bases_path = '/content/drive/MyDrive/MLi/Course/GEO876/point2.shp'

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


### Prepare the python libraries

In [ ]:
from datetime import datetime, timedelta
import pandas as pd
import geopandas as gpd
import numpy as np
import requests
import time
from io import StringIO
import folium
from folium import Marker, LayerControl, FeatureGroup
from folium.plugins import HeatMap
from shapely.geometry import Point
from bokeh.plotting import figure, show, output_notebook
from bokeh.layouts import gridplot
from bokeh.models import BoxAnnotation
import ipywidgets as widgets
from IPython.display import display, clear_output
import branca

##  1. Fetch, Analyze, and Visualize Wildfire Data.

This code defines a class **WildfireDataFetcher** that fetches wildfire data for a given country (in this case, Russia) using the NASA FIRMS Web Fire Mapper API. The data includes the acquisition date and geographic coordinates of detected wildfires.

**Class WildfireDataFetcher**:


Purpose: To fetch and display wildfire data.


Methods:


**__init__**: Initializes the fetcher with the API key, start date, and end date. It sets up the base URL for the API request.


**fetch_data_for_date**: Fetches data for a specific date. It handles API errors and invalid responses.

**fetch_all_data**: Fetches data for all dates from the start date to the end date.


**update_map**: Filters the fetched data based on a date range and displays it on a Folium map.


**interactive_map**: Creates an interactive widget to choose date ranges for the map display.

In [ ]:
class WildfireDataFetcher:
    def __init__(self, map_key, start_date, end_date=None):
        self.map_key = map_key
        self.start_date = start_date
        self.end_date = end_date if end_date else datetime.now()
        self.base_url = "https://firms.modaps.eosdis.nasa.gov/api/country/csv/{}/VIIRS_NOAA20_NRT/RUS/1/{}"
        self.wildfire_df = pd.DataFrame()

    def fetch_data_for_date(self, date):
        formatted_date = date.strftime("%Y-%m-%d")
        while True:
            try:
                response = requests.get(self.base_url.format(self.map_key, formatted_date))
                if "Invalid MAP_KEY" in response.text:
                    print(f"Invalid MAP_KEY detected for {formatted_date}. Waiting for 10 minutes before retrying.")
                    time.sleep(600)  # Wait for 10 minutes
                    continue  # Continue the while loop

                response.raise_for_status()
                decoded_content = response.content.decode('utf-8')
                df = pd.read_csv(StringIO(decoded_content))
                df['acq_date'] = pd.to_datetime(df['acq_date'])
                return df
            except requests.exceptions.HTTPError as e:

                print(f"HTTP error fetching data for {formatted_date}: {e}")
                return None
            except Exception as e:
                print(f"Error fetching data for {formatted_date}: {e}")
                return None

    def fetch_all_data(self):
        current_date = self.start_date
        while current_date <= self.end_date:
            df = self.fetch_data_for_date(current_date)
            if df is not None:
                self.wildfire_df = pd.concat([self.wildfire_df, df])
            current_date += timedelta(days=1)

    def update_map(self, start_date, end_date):
        filtered_data = self.wildfire_df[(self.wildfire_df['acq_date'] >= pd.to_datetime(start_date)) &
                                         (self.wildfire_df['acq_date'] <= pd.to_datetime(end_date))]
        if filtered_data.empty:
            print("No data available for the selected date range.")
            return

        m = folium.Map(location=[filtered_data['latitude'].mean(), filtered_data['longitude'].mean()], zoom_start=3)
        for idx, row in filtered_data.iterrows():
            folium.CircleMarker(
                location=[row['latitude'], row['longitude']],
                radius=2,
                popup=f"{row['country_id']}: {row['acq_date']}",
                color='red',
                fill=True,
                fill_color='red'
            ).add_to(m)
        display(m)

    def interactive_map(self):
        start_date_picker = widgets.DatePicker(description='Start Date', value=self.start_date)
        end_date_picker = widgets.DatePicker(description='End Date', value=self.end_date)

        widgets.interact(self.update_map, start_date=start_date_picker, end_date=end_date_picker)

# Usage example
map_key = '51d78b7011b45e92e9f253d2e27c397d'
start_date = datetime(2022, 2, 22)
end_date = datetime(2022, 2, 28)

fetcher = WildfireDataFetcher(map_key, start_date, end_date)
fetcher.fetch_all_data()
fetcher.interactive_map()


interactive(children=(DatePicker(value=datetime.datetime(2022, 2, 22, 0, 0), description='Start Date'), DatePi…

## 2. Generate Heatmap Data including **bright_ti4** as Intensity

**Data Preparation**:    
Retrieves wildfire data (wildfire_df) from a previously created fetcher object.
Constructs a dataset (heat_data) for the heat map. Each data point includes latitude, longitude, and bright_ti4 (brightness temperature from the VIIRS instrument onboard the NOAA-20 satellite) values. The bright_ti4 value is used as the intensity measure for the heat map.

**Map Creation**:   
Initializes a Folium map centered at coordinates [51, 30] with a zoom level of 5.  

**Heat Map Generation**:   
Creates a heat map from the heat_data and adds it to the Folium map. This heat map visually represents the concentration and intensity of wildfires.   

**Color Scale Creation**:   
Generates a color scale (legend) using branca.colormap.LinearColormap, which reflects the range of brightness intensities (from min_bright_ti4 to max_bright_ti4). This scale helps interpret the heat map colors in terms of wildfire intensity.

**Display Map**:   
Renders the interactive Folium map with the heat map and custom legend.and custom legend.

In [ ]:
wildfire_df = fetcher.wildfire_df

# Generate heat map data including the 'bright_ti4' value as intensity
heat_data = [[row['latitude'], row['longitude'], row['bright_ti4']] for index, row in wildfire_df.iterrows()]

# Create a map object
m = folium.Map(location=[51, 30], zoom_start=5)

# Create a heat map and add it to the map object
HeatMap(heat_data).add_to(m)

# Get the minimum and maximum values of 'bright_ti4'
min_bright_ti4 = wildfire_df['bright_ti4'].min()
max_bright_ti4 = wildfire_df['bright_ti4'].max()

# Create a color scale
colormap = branca.colormap.LinearColormap(colors=['blue', 'lime', 'yellow', 'red'],
                                          vmin=min_bright_ti4, vmax=max_bright_ti4,
                                          caption='Brightness Intensity')

# Add the color scale to the map
colormap.add_to(m)

# Customize the position and content of the legend using HTML and JavaScript
legend_html = f'''
     <div style="position: fixed;
                 bottom: 50px; right: 50px; width: 150px; height: 80px;
                 background-color: rgba(255, 255, 255, 0.8);
                 border-radius: 5px;
                 box-shadow: 0 0 15px rgba(0, 0, 0, 0.2);
                 z-index:9999;
                 font-size:14px;
                 line-height: 20px;
                 padding: 10px;">
                 &nbsp; Brightness Legend<br>
                 &nbsp; Max: {max_bright_ti4}<br>
                 &nbsp; Min: {min_bright_ti4}
      </div>
     '''
m.get_root().html.add_child(folium.Element(legend_html))

# Display the map
m


##  3. Analyzing and Visualizing the Proximity of Wildfires to Military Bases.

The code snippet provided is a Python class named **MilitaryBaseWildfireAnalyzer**, designed for analyzing and visualizing the proximity of wildfires to military bases. Here's a detailed explanation:

**Class: MilitaryBaseWildfireAnalyzer**
Purpose: Analyze the count of wildfires within a specified range of military bases and visualize the data on an interactive map.

Initialization (__init__):

Initializes the class with the path to a shapefile of military bases, a DataFrame containing wildfire data (wildfire_df), and a range in kilometers (range_km).
Calls self.add_wildfires_count_to_military_bases() to process and add wildfire count data to the military bases.

**Method: add_wildfires_count_to_military_bases**:

Reads the military bases from the shapefile (military_bases_shp) using geopandas.
Converts the wildfire DataFrame into a GeoDataFrame, setting the coordinate reference system (CRS) to EPSG:4326.
Projects both the military bases and wildfire data to a uniform UTM coordinate system for accurate distance calculations.
Buffers the military base locations by the specified range (in meters) and performs a spatial join with the wildfire data.
Counts the number of wildfires near each military base and adds this information as a new column (wildfire_count) to the military bases GeoDataFrame.
Returns the updated GeoDataFrame, reprojected to EPSG:4326.

**Method: create_map**:

Creates an interactive Folium map.
Segments the military bases into different categories based on wildfire count (high_fire, low_fire, no_fire) and adds them as separate layers to the map.
Each military base is marked with a folium Marker, colored based on the wildfire count, and includes a popup with the base name and wildfire count.
Adds a LayerControl to the map for toggling between the different wildfire count categories.
Uses custom JavaScript to ensure that the layer control panel is expanded by default.
Returns the created Folium map.

In [ ]:
class MilitaryBaseWildfireAnalyzer:
    def __init__(self, military_bases_shp, wildfire_df, range_km):
        # Initializing the class with shapefile, wildfire data, and analysis range
        self.military_bases_shp = military_bases_shp
        self.wildfire_df = wildfire_df
        self.range_km = range_km
        # Adding wildfire counts to military bases
        self.military_bases_with_counts = self.add_wildfires_count_to_military_bases()

    def add_wildfires_count_to_military_bases(self):
        # Read the military bases shapefile
        military_bases = gpd.read_file(self.military_bases_shp)

        # Create a GeoDataFrame for wildfire data
        wildfire_geo = gpd.GeoDataFrame(
            self.wildfire_df,
            geometry=gpd.points_from_xy(self.wildfire_df.longitude, self.wildfire_df.latitude),
            crs='EPSG:4326'
        )

        # Define the UTM CRS based on the provided zone
        utm_zone = 21032
        utm_crs = f'EPSG:{utm_zone}'

        # Project both datasets to the UTM CRS
        military_bases = military_bases.to_crs(utm_crs)
        wildfire_geo = wildfire_geo.to_crs(utm_crs)
        # Buffer the military base points by the specified range in meters
        military_bases['buffered'] = military_bases.geometry.buffer(self.range_km * 1000)

        # Perform a spatial join between wildfires and buffered military bases
        buffered_bases = military_bases.set_geometry('buffered')
        joined = gpd.sjoin(wildfire_geo, buffered_bases, how='inner', op='intersects')

        # Count the number of wildfires for each military base
        wildfire_counts = joined.groupby('index_right').size()
        # Add a 'wildfire_count' column to the military bases GeoDataFrame
        military_bases['wildfire_count'] = military_bases.index.map(wildfire_counts).fillna(0).astype(int)
        # Drop the 'buffered' column as it's no longer needed
        military_bases = military_bases.drop(columns=['buffered'])

        # Return the updated GeoDataFrame with wildfire counts
        return military_bases.to_crs(epsg=4326)

    def create_map(self):
        m = folium.Map(location=[51, 30], zoom_start=3)
        max_count = self.military_bases_with_counts['wildfire_count'].max()

        all_data = FeatureGroup(name='All Data')
        high_fire = FeatureGroup(name='High Wildfire')
        low_fire = FeatureGroup(name='Low Wildfire')
        no_fire = FeatureGroup(name='No Wildfire')

        for _, row in self.military_bases_with_counts.iterrows():
            popup_text = f"Name: {row['Name']}, Wildfires: {row['wildfire_count']}"

            if row['wildfire_count'] > 10:
                icon_color = 'red'
                Marker(location=[row.geometry.y, row.geometry.x], popup=popup_text,
                       icon=folium.Icon(color=icon_color, icon='fire')).add_to(high_fire)
            elif row['wildfire_count'] > 0:
                icon_color = 'orange'
                Marker(location=[row.geometry.y, row.geometry.x], popup=popup_text,
                       icon=folium.Icon(color=icon_color, icon='fire')).add_to(low_fire)
            else:
                icon_color = 'green'
                Marker(location=[row.geometry.y, row.geometry.x], popup=popup_text,
                       icon=folium.Icon(color=icon_color, icon='fire')).add_to(no_fire)

            Marker(location=[row.geometry.y, row.geometry.x], popup=popup_text,
                   icon=folium.Icon(color=icon_color, icon='fire')).add_to(all_data)

        all_data.add_to(m)
        high_fire.add_to(m)
        low_fire.add_to(m)
        no_fire.add_to(m)
        layer_control = LayerControl()
        layer_control.add_to(m)
        m.get_root().html.add_child(folium.Element("""
            <script>
                $(document).ready(function() {
                    $(".leaflet-control-layers").addClass("leaflet-control-layers-expanded");
                });
            </script>
        """))
        return m


# Example usage
range_km = 30
analyzer = MilitaryBaseWildfireAnalyzer(military_bases_path, wildfire_df, range_km)
map_ = analyzer.create_map()
map_


<ipython-input-18-ce8446a335f8>:91: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  analyzer = MilitaryBaseWildfireAnalyzer(military_bases_path, wildfire_df, range_km)


***Analysis***   

**Military Base Distribution**: The concentration of military facilities along the borders reinforces the strategic placement of these bases, likely reflecting the historical and current defense policies of Russia. The denser clustering of bases in the Western part of Russia, particularly around the border with Ukraine, suggests a region of heightened military significance.

**Fire Incidents Near Military Bases**: While there are several areas of note, the region bordering Georgia stands out with a higher frequency of wildfires. This could point to environmental factors or operational activities unique to this area that might increase the risk of fire.e.

## 4. Analysis of Wildfire Proximity to Military Bases

This code snippet generates two types of plots—a **boxplot** and a **histogram—using** Bokeh.


**Functionality**:


**Boxplot**: Visualizes the spread and central tendency of the distances from wildfire locations to the nearest military base.
Displays the interquartile range (IQR), median (Q2), and potential outliers using the scatter method for the median and quad method for the IQR box.
The whiskers (the lines extending from the box) represent the range of the data, with the ends set at 1.5 * IQR above Q3 and below Q1, which are the typical thresholds for identifying outliers.


**Histogram**:Shows the frequency distribution of the distances from wildfire locations to the nearest military base.
Uses the quad method to create the bars of the histogram, which depict how many wildfires fall within certain distance intervals.

In [21]:
output_notebook()  # Display in a Jupyter notebook

wildfire_geo = gpd.GeoDataFrame(wildfire_df,geometry=gpd.points_from_xy(wildfire_df.longitude,wildfire_df.latitude),crs='EPSG:4326')
military_bases = gpd.read_file(military_bases_path)
wildfire_geo['nearest_base_dist'] = wildfire_geo.geometry.apply(
    lambda x: military_bases.distance(x).min()
)
# Calculate quartiles and interquartile range (IQR) for the boxplot
q1 = wildfire_geo['nearest_base_dist'].quantile(0.25)
q2 = wildfire_geo['nearest_base_dist'].quantile(0.50)
q3 = wildfire_geo['nearest_base_dist'].quantile(0.75)
iqr = q3 - q1
upper = q3 + 1.5 * iqr
lower = q1 - 1.5 * iqr

# Create a box plot
box_plot = figure(title='Boxplot of Distances from Wildfire Locations to the Nearest Military Base',
                  background_fill_color="#efefef", toolbar_location=None)
box_plot.quad(top=[q3], bottom=[q1], left=[0.45], right=[0.55], line_color="black")
box_plot.segment(x0=[0.5], y0=[lower], x1=[0.5], y1=[upper], line_color="black")
box_plot.scatter(x=[0.5], y=[q2], size=10, fill_color="white", line_color="black", marker='circle')

# Add whiskers as annotations
whisker_up = BoxAnnotation(top=upper, bottom=q3, fill_alpha=0.1, fill_color='black')
whisker_down = BoxAnnotation(bottom=lower, top=q1, fill_alpha=0.1, fill_color='black')
box_plot.add_layout(whisker_up)
box_plot.add_layout(whisker_down)

# Add y-axis label indicating the units are kilometers
box_plot.yaxis.axis_label = "Distance (km)"

# Create a histogram
hist, edges = np.histogram(wildfire_geo['nearest_base_dist'], bins=30)
hist_plot = figure(title='Histogram of Distances from Wildfire Locations to the Nearest Military Base',
                   background_fill_color="#fafafa", toolbar_location=None)
hist_plot.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:], fill_color="#3B8686", line_color="white")

# Add x-axis label indicating the units are kilometers
hist_plot.xaxis.axis_label = "Distance (km)"
hist_plot.yaxis.axis_label = "Frequency"

# Grid layout - place the plots side by side
grid = gridplot([[box_plot, hist_plot]])

show(grid)

<ipython-input-21-9b756617eec5>:6: UserWarning: Geometry is in a geographic CRS. Results from 'distance' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  lambda x: military_bases.distance(x).min()


***Analysis***: The boxplot and histogram suggest that most wildfires are concentrated within a certain proximity to military bases, with fewer cases occurring at greater distances. The data distribution is right-skewed, with potential clusters of wildfire occurrences at specific distances. This information could be vital for planning military base defenses against wildfires and allocating resources for firefighting and prevention efforts.  
The specific interpretations of distance values are limited without axis labels, and actual data points are not visible on the boxplot to assess the presence of outliers or the exact distribution. These visualizations are effective for identifying overall trends but require more detailed axis labeling for a precise analysis.

**Boxplot Analysis**:   
The boxplot visualizes the distribution of distances from wildfire locations to the nearest military base.   
*Cral Line in the Box (White Dot)*: This represents the median distance. Its position suggests the middle value of the data is relatively low, implying that at least half of the wildfires are located close to military bases.  
*Box Length*: The box represents the interquartile range (IQR), indicating that half of the wildfires occur within this range of distances. A short box would suggest that distances are generally consistent, whereas a long box would indicate more variability.   
*Whiskers*: These indicate the range of the data. If the whiskers are long, this could suggest there are wildfires that are a significant distance from military bases.   
*Outliers*: Not clearly visible in the image, but any points outside the whiskers would be considered outliers, indicating wildfires at exceptionally far or close distances.

**Histogram Analysis**:   
The histogram shows the frequency distribution of the same distance data.   
*Tall Bar on the Left*: Indicates a high frequency of wildfires occurring within a short distance from the military bases.   
*Data Skewness*: The distribution seems right-skewed, meaning there are fewer wildfires at greater distances from military bases.   
*Gaps and Spikes*: There are gaps in the data, followed by spikes, which could indicate clusters of distances where wildfires are more or less common.  ce distribution.